In [1]:
%pylab inline
%config InlineBackend.figure_format = 'svg'

Populating the interactive namespace from numpy and matplotlib


In [2]:
import h5py
import group_data as gd
import numpy as np
import pylab as plb

In [3]:
sig_mtrx_filename = 'extracted_step_trans_yaw.hdf5'

In [4]:
data = h5py.File(sig_mtrx_filename)

In [5]:
data_arrays = dict()

In [6]:
for key,value in data.items():
    data_arrays[key] = np.array(value)

In [ ]:
cell_dict = dict()


In [7]:
def calc_cell_stats(data,trial_name = 'flow_right',sig_key = 'Ph1',group = 'GMR22H05'):
    stats = list()
    for fly in gd.swarms[group].flies:
        selection = (data_arrays['signal_names'] == sig_key) & \
                    (data_arrays['fly_numbers'] == fly.fly_num) & \
                    (data_arrays['trial_names'] == trial_name)
        stats.append(np.median(data_arrays['signal_data'][selection,:],axis = 0))
    return stats

In [51]:
def plot_cell(**kwargs):
    transform = kwargs.pop('transform',lambda x:x)
    ybound = kwargs.pop('ybound',(0,1.5))
    clip_on = kwargs.pop('clip_on',False)
    lspine = kwargs.pop('lspine',False)
    
    stats = calc_cell_stats(data,**kwargs)
    ub = transform(np.nanpercentile(stats,75,axis = 0))
    lb = transform(np.nanpercentile(stats,25,axis = 0))
    me = transform(np.nanpercentile(stats,50,axis = 0))
    times = np.linspace(0,23,len(ub))
    fill_between(times,ub,lb,lw =0,alpha = 0.2,clip_on = clip_on)
    plot(times,me,lw =0.5,alpha = 0.5,clip_on = clip_on)
    gca().set_ybound(ybound)
    gca().spines['bottom'].set_visible(False)
    gca().spines['left'].set_visible(lspine)
    gca().spines['top'].set_visible(False)
    gca().spines['right'].set_visible(False)
    [x.set_visible(False) for x in plb.gca().get_xticklabels()]
    [y.set_visible(False) for y in plb.gca().get_yticklabels()]#.set_visible(False)
    [x.set_visible(False) for x in plb.gca().get_xticklines()]
    [y.set_visible(False) for y in plb.gca().get_yticklines()]
    if lspine:gca().set_ylabel(kwargs['sig_key'])

In [52]:
import matplotlib.gridspec as gridspec
gs = gridspec.GridSpec(len(sig_plot_args)*5, len(trial_list))

In [77]:
sig_plot_args = [ {'sig_key':'wb_frequency',
                   'sig_scale':50,
                   'sig_start':75,   
                   'row':0,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'Ph1',
                   'sig_scale': 30,
                   'sig_start':45,      
                   'row':5,
                   'row_span':5,  
                   'transform':lambda x:np.rad2deg(x/5)},
                  {'sig_key':'b1',            
                   'sig_scale':1.0,
                   'sig_start':0,   
                   'row':10,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'b2',            
                   'sig_scale':1.0,
                   'sig_start':0, 
                   'row':15,
                   'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'b3',            
                   'sig_scale':1.0,
                   'sig_start':0,    
                   'row':20,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'i1',            
                   'sig_scale':1.0,
                   'sig_start':0,    
                   'row':25,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'i2',            
                   'sig_scale':1.0,
                   'sig_start':0,      
                   'row':30,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'iii1',          
                   'sig_scale':1.0,
                   'sig_start':0,     
                   'row':35,'row_span':2,  
                   'transform':lambda x:x},
                  {'sig_key':'iii24',         
                   'sig_scale':1.0,
                   'sig_start':0,   
                   'row':40,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'iii3',          
                   'sig_scale':1.0,
                   'sig_start':0,  
                   'row':45,'row_span':5,  
                   'transform':lambda x:x},
                  {'sig_key':'hg1',           
                   'sig_scale':1.0,
                   'sig_start':0,     
                   'row':50,'row_span':5, 
                   'transform':lambda x:x},
                  {'sig_key':'hg2',           
                   'sig_scale':1.0,
                   'sig_start':0,   
                   'row':55,'row_span':5, 
                   'transform':lambda x:x},
                  {'sig_key':'hg3',           
                   'sig_scale':1.0,
                   'sig_start':0,   
                   'row':60,'row_span':5, 
                   'transform':lambda x:x},
                  {'sig_key':'hg4',           
                   'sig_scale':1.0,
                   'sig_start':0,    
                   'row':65,'row_span':5, 
                   'transform':lambda x:x}]

trial_list = ['flow_left','flow_right','ascending','descending','progressive','regressive']

In [72]:
figure(figsize = (8,10))
for kwargs in sig_plot_args:
    row = kwargs.pop('row')
    row_span = kwargs.pop('row_span')
    for col,trial_name in enumerate(trial_list):
        #print kwargs.keys()
        subplot(gs[row:row+row_span-1,col])
        gca().set_axis_bgcolor('none')
        kwargs['trial_name'] = trial_name
        kwargs['clip_on'] = False
        kwargs['lspine'] = col == 0
        plot_cell(**kwargs)